In [1]:
!pip install nltk
!pip install numpy
!pip install torch
!pip install torchtext
!pip install pandas
!pip install scikit-learn
!pip install tqdm

In [2]:
import nltk
import torch
import pickle
import numpy as np
import pandas as pd
import torch.nn as nn
from tqdm import tqdm
import torch.optim as optim
from collections import Counter
from scipy.sparse import lil_matrix
from torch.utils.data import Dataset
from sklearn.utils.extmath import randomized_svd
from torchtext.vocab import build_vocab_from_iterator
from torch.utils.data import DataLoader, TensorDataset
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score, confusion_matrix

### Download NLTK Tokenizer

In [3]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/harshbansal/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

## Checking for Optimal Available Device

In [4]:
device = torch.device('mps' if torch.backends.mps.is_available() else 'cpu')
device

device(type='mps')

## Read Data from CSV

In [5]:
trainDataPath = "train.csv"
df = pd.read_csv(trainDataPath)
df.head()

Class Index                                        Description
0            3  Reuters - Short-sellers, Wall Street's dwindli...
1            3  Reuters - Private investment firm Carlyle Grou...
2            3  Reuters - Soaring crude prices plus worries\ab...
3            3  Reuters - Authorities have halted oil export\f...
4            3  AFP - Tearaway world oil prices, toppling reco...

In [6]:
corpus = df["Description"].apply(nltk.word_tokenize)

In [7]:
corpus

0         [Reuters, -, Short-sellers, ,, Wall, Street, '...
1         [Reuters, -, Private, investment, firm, Carlyl...
2         [Reuters, -, Soaring, crude, prices, plus, wor...
3         [Reuters, -, Authorities, have, halted, oil, e...
4         [AFP, -, Tearaway, world, oil, prices, ,, topp...
                                ...                        
119995    [KARACHI, (, Reuters, ), -, Pakistani, Preside...
119996    [Red, Sox, general, manager, Theo, Epstein, ac...
119997    [The, Miami, Dolphins, will, put, their, court...
119998    [PITTSBURGH, at, NY, GIANTS, Time, :, 1:30, p....
119999    [INDIANAPOLIS, --, All-Star, Vince, Carter, wa...
Name: Description, Length: 120000, dtype: object

In [8]:
sentences = corpus[:40000]

In [9]:
sentences

0        [Reuters, -, Short-sellers, ,, Wall, Street, '...
1        [Reuters, -, Private, investment, firm, Carlyl...
2        [Reuters, -, Soaring, crude, prices, plus, wor...
3        [Reuters, -, Authorities, have, halted, oil, e...
4        [AFP, -, Tearaway, world, oil, prices, ,, topp...
                               ...                        
39995    [The, seven-times, Formula, One, champion, spu...
39996    [Australia, #, 39, ;, s, Todd, Woodbridge, #, ...
39997    [Police, have, been, given, more, time, to, qu...
39998    [Francoise, Sagan, ,, the, rebellious, French,...
39999    [UnanimousCoward, writes, quot, ;, A, spokespe...
Name: Description, Length: 40000, dtype: object

## Build Dataset and Vocabulary

In [10]:
class EntityDataset(Dataset):
    def __init__(self, data, vocabulary=None):
        """Initialize the dataset."""
        self.sentences = data

        if not isinstance(data, pd.Series):
            raise TypeError("Input data must be a Pandas Series.")

        if vocabulary is not None:
            self.vocabulary = vocabulary
        else:
            self.vocabulary = build_vocab_from_iterator(self.sentences)

        self.index_to_word = self.vocabulary.get_itos()

        self.window_size = 1
        self.co_occurrence_matrix = self._build_co_occurrence_matrix()

    def _build_co_occurrence_matrix(self):
        """Builds the co-occurrence matrix from the dataset."""
        vocab_size = len(self.vocabulary)
        co_occurrence_matrix = lil_matrix((vocab_size, vocab_size), dtype=np.float32)

        for sentence in self.sentences:
            indices = [self.vocabulary[word] for word in sentence if word in self.vocabulary]
            for i, center_word_index in enumerate(indices):
                for j in range(max(0, i - self.window_size), min(len(indices), i + self.window_size + 1)):
                    if i != j:
                        context_word_index = indices[j]
                        co_occurrence_matrix[center_word_index, context_word_index] += 1

        # Convert LIL matrix to CSR format for efficient computation
        co_occurrence_matrix = co_occurrence_matrix.tocsr()

        return co_occurrence_matrix

    def __len__(self):
        """Returns number of datapoints."""
        return len(self.sentences)

    def __getitem__(self, index):
        """Get the datapoint at `index`."""
        sentence = self.sentences[index]
        sentence_indices = [self.vocabulary[word] for word in sentence]
        return torch.tensor(sentence_indices)

    def get_index_to_word(self, index):
        """Get the word corresponding to a given index."""
        return self.index_to_word[index]

    def get_word_to_index(self, word):
        """Get the word corresponding to a given index."""
        return self.vocabulary[word]


### Initialise Vocabulary

In [11]:
dataset = EntityDataset(sentences)

### Obtain the Co-Occurence Matrix

In [12]:
co_occurrence_matrix = dataset.co_occurrence_matrix
print("Dimensions of co-occurrence matrix:", co_occurrence_matrix.shape)
print(co_occurrence_matrix)

Dimensions of co-occurrence matrix: (57588, 57588)
  (0, 0)	4.0
  (0, 1)	4137.0
  (0, 2)	1.0
  (0, 3)	2435.0
  (0, 4)	1.0
  (0, 5)	6533.0
  (0, 6)	7165.0
  (0, 7)	1314.0
  (0, 8)	97.0
  (0, 9)	2161.0
  (0, 10)	82.0
  (0, 11)	2680.0
  (0, 12)	20.0
  (0, 13)	1.0
  (0, 14)	908.0
  (0, 15)	11.0
  (0, 16)	4.0
  (0, 17)	1.0
  (0, 18)	40.0
  (0, 19)	1245.0
  (0, 20)	1.0
  (0, 21)	34.0
  (0, 22)	986.0
  (0, 23)	2029.0
  (0, 24)	228.0
  :	:
  (57575, 1126)	1.0
  (57576, 6)	1.0
  (57576, 1400)	1.0
  (57577, 7)	1.0
  (57577, 65)	1.0
  (57578, 3561)	1.0
  (57578, 3593)	1.0
  (57579, 41)	1.0
  (57579, 27018)	1.0
  (57580, 99)	1.0
  (57580, 435)	1.0
  (57581, 435)	1.0
  (57581, 2179)	1.0
  (57582, 2)	1.0
  (57582, 7)	1.0
  (57583, 2)	1.0
  (57583, 113)	1.0
  (57584, 1)	1.0
  (57584, 32)	1.0
  (57585, 7)	1.0
  (57585, 4909)	1.0
  (57586, 15)	1.0
  (57586, 37)	1.0
  (57587, 12)	1.0
  (57587, 1750)	1.0


## Applying SVD to Co-Occurence Matrix

In [13]:
k = 300
U, s, Vt = randomized_svd(co_occurrence_matrix, n_components=k)

In [14]:
print(f"Shape of U: {U.shape}")
print(f"Shape of s: {s.shape}")
print(f"Shape of Vt: {Vt.shape}")

Shape of U: (57588, 300)
Shape of s: (300,)
Shape of Vt: (300, 57588)


In [15]:
word_to_index = dataset.vocabulary.get_stoi()

word_embeddings = {}
for word, index in word_to_index.items():
    word_embeddings[word] = U[index]

In [16]:
word_embeddings

{'zzzzzz': array([ 2.41732614e-05,  2.54156494e-05, -7.44845556e-06,  5.08297887e-07,
        -2.04671051e-06,  9.56119475e-05, -9.74026188e-05,  1.62870765e-05,
         2.35702623e-06,  4.58701061e-06,  1.01373132e-06, -3.96126416e-05,
        -1.51275735e-05, -6.24114136e-06,  5.15627471e-05, -8.52584492e-07,
         2.75084994e-06,  4.49211893e-06,  2.92145046e-06, -2.21912296e-06,
        -2.16293256e-06,  1.39619758e-07, -3.45299372e-06,  5.63956155e-06,
         5.28464989e-06,  1.88314311e-06, -3.17155127e-07, -3.56883197e-06,
        -8.25582219e-07, -5.71575902e-06, -7.85570228e-06, -6.68948496e-06,
        -4.41915881e-06, -5.55613951e-06,  2.67135351e-06, -2.26467023e-09,
         2.26839120e-07,  1.40958116e-06, -6.73976842e-07, -8.21408946e-07,
         1.27127873e-06,  4.76793093e-06,  3.21111656e-07, -1.13425795e-05,
        -3.97313943e-06, -7.23300127e-06, -5.11823373e-06,  8.18372610e-06,
         6.48696869e-06,  5.96901873e-06, -4.11360497e-06, -3.72172644e-06,
  

### Saving the Embeddings and the Vocabulary

In [17]:
# Save vocabulary to a pickle file
with open('svd-vocabulary.pkl', 'wb') as f:
    pickle.dump(dataset.vocabulary, f)

# Save word embeddings to a pickle file
with open('svd-word-vectors.pkl', 'wb') as f:
    pickle.dump(word_embeddings, f)

torch.save(word_embeddings,"svd-word-vectors.pt")
torch.save(dataset.vocabulary,"svd-vocabulary.pt")


## Training RNN on Word Embeddings

### Extracting the Labels

In [18]:
labels = df["Class Index"][:len(sentences)].values - 1
labels

array([2, 2, 2, ..., 0, 0, 2])

### Generate Sentence Embeddings

In [19]:
def generate_sentence_embeddings(word_embeddings, sentences):
    sentence_embeddings = []
    for sentence in sentences:
        embeddings = [torch.tensor(word_embeddings[word]) for word in sentence if word in word_embeddings]
        if embeddings:
            # Average the embeddings to get the sentence embedding
            sentence_embedding = torch.mean(torch.stack(embeddings), dim=0)
            sentence_embeddings.append(sentence_embedding)
    return torch.stack(sentence_embeddings)

In [20]:
sentence_embeddings = generate_sentence_embeddings(word_embeddings,sentences)
print(np.shape(sentence_embeddings))

torch.Size([40000, 300])


In [21]:
labels = torch.Tensor(labels)
labels

tensor([2., 2., 2.,  ..., 0., 0., 2.])

### Defining the LSTM Model

In [22]:
class LSTMModel(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(LSTMModel, self).__init__()
        self.hidden_size = hidden_size
        self.lstm = nn.LSTM(input_size, hidden_size)
        self.linear1 = nn.Linear(hidden_size, 128)  
        self.linear2 = nn.Linear(128, output_size) 

    def forward(self, x):
        out, _ = self.lstm(x.unsqueeze(1))  
        out = torch.relu(self.linear1(out[:, -1, :]))  
        out = self.linear2(out)
        return out


In [23]:
sentence_embeddings = sentence_embeddings.to(device)
labels = labels.to(device)

### Define Hyperparameters

In [24]:
input_size = sentence_embeddings.size(1) 
hidden_size = 256
output_size = 4  
learning_rate = 0.001
num_epochs = 25

### Create DataLoader

In [25]:
dataset = TensorDataset(sentence_embeddings, labels)
dataset

In [26]:
loader = DataLoader(dataset, batch_size=100, shuffle=True)
loader

### Initialize Model, Loss Function, and Optimizer

In [27]:
model = LSTMModel(input_size, hidden_size, output_size).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=learning_rate)

### Training Loop

In [28]:
for epoch in range(num_epochs):
    running_loss = 0.0
    model.train()  # Set model to training mode
    for inputs, label in tqdm(loader, desc=f'Epoch {epoch + 1}/{num_epochs}', leave=False):
        inputs, label = inputs.to(device), label.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, label)
        loss.backward()
        optimizer.step()

        running_loss += loss.item()

    print(f"Epoch {epoch + 1}/{num_epochs}, Loss: {running_loss / len(loader)}")

    # Evaluation on train set
    model.eval()  # Set model to evaluation mode
    train_preds = []
    train_labels = []
    for inputs, label in loader:
        inputs, label = inputs.to(device), label.to(device)
        outputs = model(inputs)
        _, predicted = torch.max(outputs, 1)
        train_preds.extend(predicted.tolist())
        train_labels.extend(label.tolist())

    train_accuracy = accuracy_score(train_labels, train_preds)
    train_f1 = f1_score(train_labels, train_preds, average='weighted')
    train_precision = precision_score(train_labels, train_preds, average='weighted')
    train_recall = recall_score(train_labels, train_preds, average='weighted')
    train_confusion = confusion_matrix(train_labels, train_preds)

    print("Train Dataset Metrics:")
    print(f"Accuracy: {train_accuracy}")
    print(f"F1 Score: {train_f1}")
    print(f"Precision: {train_precision}")
    print(f"Recall: {train_recall}")
    print("Confusion Matrix:")
    print(train_confusion)

print("Training complete")


torch.save(model,"svd-classification-model.pt")

Epoch 1/25, Loss: 1.089614659100771
Train Dataset Metrics:
Accuracy: 0.742275
F1 Score: 0.7434008428526995
Precision: 0.7486592928085772
Recall: 0.742275
Confusion Matrix:
[[8556  514  797  694]
 [1236 7597  164  900]
 [1063  143 6473 1699]
 [1187  267 1645 7065]]


Epoch 2/25, Loss: 0.6259022401273251
Train Dataset Metrics:
Accuracy: 0.792325
F1 Score: 0.7910918567607137
Precision: 0.8006178109882971
Recall: 0.792325
Confusion Matrix:
[[8186  846  499 1030]
 [ 297 8986   75  539]
 [ 662  337 6048 2331]
 [ 566  499  626 8473]]


Epoch 3/25, Loss: 0.5537646771222353
Train Dataset Metrics:
Accuracy: 0.8008
F1 Score: 0.7999058421191905
Precision: 0.802601302764979
Recall: 0.8008
Confusion Matrix:
[[7995  920  906  740]
 [ 223 9171  178  325]
 [ 450  326 7361 1241]
 [ 566  596 1497 7505]]


Epoch 4/25, Loss: 0.5298312889039516
Train Dataset Metrics:
Accuracy: 0.805775
F1 Score: 0.8070448897418044
Precision: 0.8103760367175701
Recall: 0.805775
Confusion Matrix:
[[8559  413  730  859]
 [ 614 8386  209  688]
 [ 598   98 7074 1608]
 [ 657  216 1079 8212]]


Epoch 5/25, Loss: 0.5179495879262686
Train Dataset Metrics:
Accuracy: 0.815525
F1 Score: 0.8147267463680823
Precision: 0.8156271487635646
Recall: 0.815525
Confusion Matrix:
[[8357  793  754  657]
 [ 258 9197  152  290]
 [ 511  302 7343 1222]
 [ 601  516 1323 7724]]


...

Epoch 21/25, Loss: 0.44447738751769067
Train Dataset Metrics:
Accuracy: 0.838375
F1 Score: 0.838529878999605
Precision: 0.8395277133988922
Recall: 0.838375
Confusion Matrix:
[[9121  378  473  589]
 [ 380 8926  135  456]
 [ 583  136 7223 1436]
 [ 708  262  929 8265]]


Epoch 22/25, Loss: 0.44467830680310727
Train Dataset Metrics:
Accuracy: 0.832725
F1 Score: 0.8313036217212044
Precision: 0.8331131713398862
Recall: 0.832725
Confusion Matrix:
[[9113  487  590  371]
 [ 312 9223  179  183]
 [ 559  234 7710  875]
 [ 832  521 1548 7263]]


Epoch 23/25, Loss: 0.43820105481892824
Train Dataset Metrics:
Accuracy: 0.836025
F1 Score: 0.8343455957396664
Precision: 0.8360291566610808
Recall: 0.836025
Confusion Matrix:
[[9254  557  298  452]
 [ 281 9338   66  212]
 [ 770  307 6863 1438]
 [ 873  516  789 7986]]


Epoch 24/25, Loss: 0.4371736914664507
Train Dataset Metrics:
Accuracy: 0.836425
F1 Score: 0.8367911465469109
Precision: 0.83807432213086
Recall: 0.836425
Confusion Matrix:
[[9102  358  438  663]
 [ 345 8851  130  571]
 [ 549  164 7271 1394]
 [ 693  291  947 8233]]


Epoch 25/25, Loss: 0.4380242185667157
Train Dataset Metrics:
Accuracy: 0.8413
F1 Score: 0.8405991738249029
Precision: 0.840791823760787
Recall: 0.8413
Confusion Matrix:
[[9209  429  379  544]
 [ 339 9161   95  302]
 [ 654  227 7227 1270]
 [ 771  392  946 8055]]
Training complete


## Testing

### Read Data from CSV

In [29]:
testDataPath = "test.csv"
df_test = pd.read_csv(testDataPath)
df_test.head()

Class Index                                        Description
0            3  Unions representing workers at Turner   Newall...
1            4  SPACE.com - TORONTO, Canada -- A second\team o...
2            4  AP - A company founded by a chemistry research...
3            4  AP - It's barely dawn when Mike Fitzpatrick st...
4            4  AP - Southern California's smog-fighting agenc...

In [30]:
corpus_test = df_test["Description"].apply(nltk.word_tokenize)

In [31]:
corpus_test

0       [Unions, representing, workers, at, Turner, Ne...
1       [SPACE.com, -, TORONTO, ,, Canada, --, A, seco...
2       [AP, -, A, company, founded, by, a, chemistry,...
3       [AP, -, It, 's, barely, dawn, when, Mike, Fitz...
4       [AP, -, Southern, California, 's, smog-fightin...
                              ...                        
7595    [Ukrainian, presidential, candidate, Viktor, Y...
7596    [With, the, supply, of, attractive, pitching, ...
7597    [Like, Roger, Clemens, did, almost, exactly, e...
7598    [SINGAPORE, :, Doctors, in, the, United, State...
7599    [EBay, plans, to, buy, the, apartment, and, ho...
Name: Description, Length: 7600, dtype: object

### Extracting the Labels

In [32]:
labels_test = df_test["Class Index"].values - 1
labels_test

array([2, 3, 3, ..., 1, 2, 2])

### Generate Sentence Embeddings

In [33]:
sentence_embeddings_test = generate_sentence_embeddings(word_embeddings,corpus_test)
print(np.shape(sentence_embeddings_test))

torch.Size([7600, 300])


In [34]:
labels_test = torch.Tensor(labels_test)
print(np.shape(labels_test))

torch.Size([7600])


In [35]:
# Convert test data to PyTorch tensors
sentence_embeddings_test = sentence_embeddings_test.to(device)
labels_test = labels_test.to(device)

# Create DataLoader for test data
test_dataset = TensorDataset(sentence_embeddings_test, labels_test)
test_loader = DataLoader(test_dataset, batch_size=100, shuffle=False)

# Evaluation loop
model.eval()  
test_preds = []
test_labels = []

with torch.no_grad(): 
    for inputs, labels in test_loader:
        inputs, labels = inputs.to(device), labels.to(device)
        outputs = model(inputs)
        _, predicted = torch.max(outputs, 1)       
    
        test_preds.extend(predicted.tolist())
        test_labels.extend(labels.tolist())  # Fix here, change 'label' to 'labels'

    test_accuracy = accuracy_score(test_labels, test_preds)
    test_f1 = f1_score(test_labels, test_preds, average='weighted')
    test_precision = precision_score(test_labels, test_preds, average='weighted')
    test_recall = recall_score(test_labels, test_preds, average='weighted')
    test_confusion = confusion_matrix(test_labels, test_preds)

    print("Test Dataset Metrics:")
    print(f"Accuracy: {test_accuracy}")
    print(f"F1 Score: {test_f1}")
    print(f"Precision: {test_precision}")
    print(f"Recall: {test_recall}")
    print("Confusion Matrix:")
    print(test_confusion)

Test Dataset Metrics:
Accuracy: 0.8103947368421053
F1 Score: 0.8093349969022873
Precision: 0.8098688808050192
Recall: 0.8103947368421053
Confusion Matrix:
[[1624   91   80  105]
 [  98 1717   28   57]
 [ 127   65 1390  318]
 [ 142  121  209 1428]]
